In [1]:
import pickle
#Run this with >bokeh serve --show TextAnalysis.ipynb
import pandas as pd
import numpy as np
from collections import Counter
import warnings
warnings.filterwarnings("ignore")
from bokeh.io import curdoc,curstate
from bokeh.layouts import widgetbox
import time

from bokeh.layouts import layout,column,row
from bokeh.plotting import figure, show, output_file
from bokeh.models import ColumnDataSource,Slider
from bokeh.palettes import Spectral6

from bokeh.models.widgets import Panel, Tabs
from bokeh.models.callbacks import CustomJS

import datashader as ds
import xarray
import time
import collections
import datashader.transfer_functions as tf

In [2]:
from bokeh.io import output_notebook, push_notebook
output_notebook()

Loading BokehJS ...

In [10]:
dict_=pickle.load(open('output_large.pkl','rb'))
print(dict_.keys())

dict_keys(['lstm_output', 'y_pred', 'y_val'])


In [48]:
lstm_output=dict_['lstm_output']
y_pred=dict_['y_pred']
y_val=dict_['y_val']
lstm_df=pd.DataFrame(lstm_output)

lstm_df['y_pred']=y_pred
lstm_df['y_val']=y_val
print(lstm_df['y_val'].value_counts())

grouped=lstm_df.groupby(['y_val'])
grouped2=lstm_df.groupby(['y_pred'])

def get_group(val_num=5):
    global grouped
    return grouped.get_group((val_num))

def get_group2(val_num=5):
    global grouped2
    return grouped2.get_group((val_num))

class4=get_group(val_num=4)
class4.reset_index(inplace=True)

class3=get_group(val_num=3)
class3.reset_index(inplace=True)

class2=get_group(val_num=2)
class2.reset_index(inplace=True)

class1=get_group(val_num=1)
class1.reset_index(inplace=True)

class0=get_group(val_num=0)
class0.reset_index(inplace=True)

print(class0.shape,class1.shape,class2.shape,class3.shape,class4.shape)

class4p=get_group2(val_num=4)
class4p.reset_index(inplace=True)

class3p=get_group2(val_num=3)
class3p.reset_index(inplace=True)

class2p=get_group2(val_num=2)
class2p.reset_index(inplace=True)

class1p=get_group2(val_num=1)
class1p.reset_index(inplace=True)

class0p=get_group2(val_num=0)
class0p.reset_index(inplace=True)


4    28279
3     6656
0     4292
2     3693
1     2552
Name: y_val, dtype: int64
(4292, 131) (2552, 131) (3693, 131) (6656, 131) (28279, 131)


In [49]:
def base_plot(x_range,y_range,tools='pan,wheel_zoom,reset'):
    p = figure(tools=tools, plot_width=600, plot_height=300,\
        x_range=x_range, y_range=y_range)   
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.add_tools(BoxZoomTool(match_aspect=True))
    return p

ndim=128
def dataframe_from_multiple_sequences(points,data):    
    ds_df=[]
    n_rows,n_cols=data.shape

    nans=np.zeros((n_rows,1))
    nans[:,0]=np.NaN
    data2=np.append(data,nans,1)
    
    for row in range(n_rows):
        df=pd.DataFrame(dict(x=np.arange(n_cols+1),y=data2[row,:]))
        ds_df.append(df)
        
    ds_df=pd.concat(ds_df)
    return ds_df
        


In [69]:
#analyse the smallest class which is class1
from datashader.bokeh_ext import InteractiveImage
from bokeh.models import BoxZoomTool


lstm_matrix=class1.iloc[:,1:-2].as_matrix()
x_range=(0,len(lstm_matrix))
y_range=(np.min(lstm_matrix),np.max(lstm_matrix))

lstm_matrixp=class1p.iloc[:,1:-2].as_matrix()
x_rangep=(0,len(lstm_matrixp))
y_rangep=(np.min(lstm_matrixp),np.max(lstm_matrixp))

print(x_range,y_range,x_rangep,y_rangep)

def create_image(x_range, y_range, w, h,lstm_matrix,cp,name):    
    #lstm_matrix=df.as_matrix()
    
    print(lstm_matrix.shape)
    df = dataframe_from_multiple_sequences(np.arange(ndim),lstm_matrix)
    cvs = ds.Canvas(plot_height=400, plot_width=600)
    agg = cvs.line(df, 'x', 'y', ds.count()) 

    
    img = tf.spread(tf.shade(agg, how='eq_hist',cmap=cp, name=name))
    return img

p1=base_plot(x_range,y_range)
p2=base_plot(x_rangep,y_rangep)
w,h=800,600
InteractiveImage(p1,lambda x_range,y_range,w,h,: create_image( x_range,y_range,w,h,lstm_matrix,\
                                                             ['pink','orange'],"True Class"))
InteractiveImage(p2,lambda x_range,y_range,w,h,: create_image( x_range,y_range,w,h,lstm_matrixp,\
                                                             ['grey','black'],"Pred class"))
show(column(p1,p2))


(0, 2552) (-1.0, 1.0) (0, 2382) (-1.0, 1.0)
(2552, 128)
(2382, 128)


In [44]:
#analyse the smallest class which is class1
from datashader.bokeh_ext import InteractiveImage
from bokeh.models import BoxZoomTool


lstm_matrix=class0.iloc[:,1:-2].as_matrix()
x_range=(0,len(lstm_matrix))
y_range=(np.min(lstm_matrix),np.max(lstm_matrix))

print(x_range,y_range)
def create_image(x_range, y_range, w, h):    
    #lstm_matrix=df.as_matrix()
    
    print(lstm_matrix.shape)
    df = dataframe_from_multiple_sequences(np.arange(ndim),lstm_matrix)
    cvs = ds.Canvas(plot_height=400, plot_width=600)
    agg = cvs.line(df, 'x', 'y', ds.count())   
    img = tf.shade(agg, how='eq_hist')
    return img

p=base_plot(x_range,y_range)
InteractiveImage(p,create_image)


(0, 4292) (-1.0000001192092896, 1.0)
(4292, 128)


In [45]:
#analyse the smallest class which is class1
from datashader.bokeh_ext import InteractiveImage
from bokeh.models import BoxZoomTool


lstm_matrix=class2.iloc[:,1:-2].as_matrix()
x_range=(0,len(lstm_matrix))
y_range=(np.min(lstm_matrix),np.max(lstm_matrix))

print(x_range,y_range)
def create_image(x_range, y_range, w, h):    
    #lstm_matrix=df.as_matrix()
    
    print(lstm_matrix.shape)
    df = dataframe_from_multiple_sequences(np.arange(ndim),lstm_matrix)
    cvs = ds.Canvas(plot_height=400, plot_width=600)
    agg = cvs.line(df, 'x', 'y', ds.count())   
    img = tf.shade(agg, how='eq_hist')
    return img

p=base_plot(x_range,y_range)
InteractiveImage(p,create_image)


(0, 3693) (-1.0000001192092896, 1.0)
(3693, 128)


In [46]:
#analyse the smallest class which is class1
from datashader.bokeh_ext import InteractiveImage
from bokeh.models import BoxZoomTool


lstm_matrix=class3.iloc[:,1:-2].as_matrix()
x_range=(0,len(lstm_matrix))
y_range=(np.min(lstm_matrix),np.max(lstm_matrix))

print(x_range,y_range)
def create_image(x_range, y_range, w, h):    
    #lstm_matrix=df.as_matrix()
    
    print(lstm_matrix.shape)
    df = dataframe_from_multiple_sequences(np.arange(ndim),lstm_matrix)
    cvs = ds.Canvas(plot_height=400, plot_width=600)
    agg = cvs.line(df, 'x', 'y', ds.count())   
    img = tf.shade(agg, how='eq_hist')
    return img

p=base_plot(x_range,y_range)
InteractiveImage(p,create_image)




(0, 6656) (-1.0, 1.0)
(6656, 128)


In [47]:
#analyse the smallest class which is class1
from datashader.bokeh_ext import InteractiveImage
from bokeh.models import BoxZoomTool


lstm_matrix=class4.iloc[:,1:-2].as_matrix()
x_range=(0,len(lstm_matrix))
y_range=(np.min(lstm_matrix),np.max(lstm_matrix))

print(x_range,y_range)
def create_image(x_range, y_range, w, h):    
    #lstm_matrix=df.as_matrix()
    
    print(lstm_matrix.shape)
    df = dataframe_from_multiple_sequences(np.arange(ndim),lstm_matrix)
    cvs = ds.Canvas(plot_height=400, plot_width=600)
    agg = cvs.line(df, 'x', 'y', ds.count())   
    img = tf.shade(agg, how='eq_hist')
    return img

p=base_plot(x_range,y_range)
InteractiveImage(p,create_image)


(0, 28279) (-1.0000001192092896, 1.0000001192092896)
(28279, 128)
